In [30]:
using CSV
using DataFrames
using Turing
using MCMCChains
using Plots
using StatsPlots
using StatsBase
using Distributions
using NPZ

## Importing ##

In [31]:
eye_area = npzread("spikeAndBehavioralData/allData/Cori_2016-12-14/eye.area.npy")
clusterids = npzread("spikeAndBehavioralData/allData/Cori_2016-12-14/spikes.clusters.npy")[:] 
spiketimes = npzread("spikeAndBehavioralData/allData/Cori_2016-12-14/spikes.times.npy")[:]
eyetimes = npzread("spikeAndBehavioralData/allData/Cori_2016-12-14/eye.timestamps.npy")


267759×2 Matrix{Float64}:
      0.0    15.9828
      1.0    15.9928
      2.0    16.0028
      3.0    16.0128
      4.0    16.0228
      5.0    16.0328
      6.0    16.0428
      7.0    16.0528
      8.0    16.0628
      9.0    16.0728
     10.0    16.0828
     11.0    16.0928
     12.0    16.1028
      ⋮    
 267747.0  2693.75
 267748.0  2693.76
 267749.0  2693.77
 267750.0  2693.78
 267751.0  2693.79
 267752.0  2693.8
 267753.0  2693.81
 267754.0  2693.82
 267755.0  2693.83
 267756.0  2693.84
 267757.0  2693.85
 267758.0  2693.86

In [32]:
eye_area

267759×1 Matrix{Float64}:
 2.0032918037677168
 2.021721870825399
 2.02494752287479
 2.0400730810940955
 2.035858513033822
 2.0594103849698406
 2.145196838133316
 2.0519775764134107
 2.1509637334731986
 2.138931611998483
 2.127941338794287
 2.1445389187645394
 2.1555536801897768
 ⋮
 3.864455045376135
 3.8772716000615697
 3.768493702322403
 3.8333892775027856
 3.8282052908543234
 3.799436770497894
 3.8412511490215024
 3.8262881549960577
 3.8383554090252847
 3.795938687762785
 3.7756243396703737
 3.7855297651654234

In [33]:
# Remove all negative areas from the eye_area data
for i in 1:length(eye_area)
    if eye_area[i] < 0
        eye_area[i] = 0
    end
end

plot(eye_area)

In [35]:
# count spikes for each cluster
unique_clusterids = sort(unique(clusterids))
nclusters = length(unique_clusterids) # number of clusters
binedges = -0.5 .+ append!(unique_clusterids,clusterids[end]+1)
h_spikecounts = StatsBase.fit(Histogram,clusterids[:],binedges)
spikecounts = h_spikecounts.weights
spikerates = spikecounts./maximum(spiketimes)

# get spike counts per timebin

dt = 1 # seconds
maxtime = maximum(eyetimes)
timebin_edges = (20:dt:maxtime-20)
nt = length(timebin_edges)
spikecount_array = Array{Int64}(undef,nclusters,nt-1)

for i = 1:nclusters
    inds = findall(clusterids.==i)
    htemp = StatsBase.fit(Histogram,spiketimes[:][inds],timebin_edges)
    spikecount_array[i,:] = htemp.weights
end

In [36]:
spikecount_array

1085×267718 Matrix{Int64}:
  2   0   0   0   3   1   5   2   1  …  0  0  0  0  0  0  0  0  0  0  0  0
  0   0   0   0   0   0   0   0   0     0  0  0  0  0  0  0  0  0  0  0  0
  0   0   1   0   0   0   0   0   0     0  0  0  0  0  0  0  0  0  0  0  0
  0   0   1   0   0   0   2   0   1     0  0  0  0  0  0  0  0  0  0  0  0
  1   2   0   4   3   0   0   0   1     0  0  0  0  0  0  0  0  0  0  0  0
  0   0   0   0   0   0   0   0   0  …  0  0  0  0  0  0  0  0  0  0  0  0
  0   0   0   0   0   0   0   0   0     0  0  0  0  0  0  0  0  0  0  0  0
  6   3   6   5   3   3   6   3   2     0  0  0  0  0  0  0  0  0  0  0  0
  0   0   1   0   1   2   0   0   1     0  0  0  0  0  0  0  0  0  0  0  0
  2   0   1   0   0   0   0   0   0     0  0  0  0  0  0  0  0  0  0  0  0
  0   0   1   0   0   0   0   0   0  …  0  0  0  0  0  0  0  0  0  0  0  0
  0   0   1   5   3   1   1   0   0     0  0  0  0  0  0  0  0  0  0  0  0
  0   0   0   0   0   0   0   0   0     0  0  0  0  0  0  0  0  0  0  0  